### Registering entities represented in grocery dataset

In FeatureByte, an "entity" models real-world objects and ideas. These entities often correspond to keys in database tables.

Taking our grocery scenario as an example, we can view "Customer", "Invoice", and "Item" as entities.

To help FeatureByte identify these entities in the data and the columns that represent them, we'll be creating and tagging these entities in this tutorial.

In [1]:
import featurebyte as fb

# Set your profile to the tutorial environment
fb.use_profile("tutorial")

catalog_name = "Grocery Dataset SDK Tutorial"
catalog = fb.Catalog.activate(catalog_name)  

11:06:58 | INFO     | SDK version: 3.2.0.dev66
INFO    :featurebyte:SDK version: 3.2.0.dev66
11:06:58 | INFO     | No catalog activated.
INFO    :featurebyte:No catalog activated.
11:06:58 | INFO     | Using profile: staging
INFO    :featurebyte:Using profile: staging
11:06:58 | INFO     | Using configuration file at: /Users/gxav/.featurebyte/config.yaml
INFO    :featurebyte:Using configuration file at: /Users/gxav/.featurebyte/config.yaml
11:06:58 | INFO     | Active profile: staging (https://staging.featurebyte.com/api/v1)
INFO    :featurebyte:Active profile: staging (https://staging.featurebyte.com/api/v1)
11:06:58 | INFO     | SDK version: 3.2.0.dev66
INFO    :featurebyte:SDK version: 3.2.0.dev66
11:06:58 | INFO     | No catalog activated.
INFO    :featurebyte:No catalog activated.
11:06:58 | INFO     | Catalog activated: Grocery Dataset SDK Tutorial
INFO    :featurebyte.api.catalog:Catalog activated: Grocery Dataset SDK Tutorial


16:05:47 | INFO     | Using configuration file at: /Users/gxav/.featurebyte/config.yaml


16:05:47 | INFO     | Active profile: tutorial (https://tutorials.featurebyte.com/api/v1)


16:05:47 | WARNING  | Remote SDK version (1.1.0.dev7) is different from local (1.1.0.dev1). Update local SDK to avoid unexpected behavior.


16:05:47 | INFO     | No catalog activated.


16:05:47 | INFO     | Catalog activated: Grocery Dataset Tutorial


As previously discussed, we'll establish the following entities:
- customer - an individual shopping at the stores
- invoice - a record of the customer's purchase
- item - individual items on the invoice
- product - products available in the store for purchase
- productgroup - the category or group a product falls under
- frenchstate - a region in France (since our dataset revolves around French grocery stores and their customers)

It's worth noting that the count of entities doesn't necessarily have to align with the number of tables. An entity is a business-oriented term, and multiple entities might be represented within a single table.

When creating an entity, you'll need to define its [serving name](https://docs.featurebyte.com/0.5/about/glossary/#entity-serving-name). This name acts as a unique identifier, particularly during preview or serving requests.

In [2]:
catalog.create_entity(name="customer", serving_names=["GROCERYCUSTOMERGUID"])
catalog.create_entity(name="invoice", serving_names=["GROCERYINVOICEGUID"])
catalog.create_entity(name="item", serving_names=["GROCERYINVOICEITEMGUID"])
catalog.create_entity(name="product", serving_names=["GROCERYPRODUCTGUID"])
catalog.create_entity(name="productgroup", serving_names=["PRODUCTGROUP"])
catalog.create_entity(name="frenchstate", serving_names=["FRENCHSTATE"])

<featurebyte.api.entity.Entity at 0x10780ca90>
{
  'name': 'frenchstate',
  'created_at': '2025-10-15T03:06:59.366000',
  'updated_at': None,
  'description': None,
  'serving_names': [
    'FRENCHSTATE'
  ],
  'catalog_name': 'Grocery Dataset SDK Tutorial'
}

Now that we've established the entities, it's time to guide FeatureByte in mapping these entities to the actual data in our tables.

In [3]:
customer_table = catalog.get_table("GROCERYCUSTOMER")
invoice_table = catalog.get_table("GROCERYINVOICE")
items_table = catalog.get_table("INVOICEITEMS")
product_table = catalog.get_table("GROCERYPRODUCT")

In [4]:
# tag the entities for the grocery customer table
customer_table.GroceryCustomerGuid.as_entity("customer")
customer_table.State.as_entity("frenchstate")

# tag the entities for the grocery invoice table
invoice_table.GroceryInvoiceGuid.as_entity("invoice")
invoice_table.GroceryCustomerGuid.as_entity("customer")

# tag the entities for the grocery items table
items_table.GroceryInvoiceItemGuid.as_entity("item")
items_table.GroceryInvoiceGuid.as_entity("invoice")
items_table.GroceryProductGuid.as_entity("product")

# tag the entities for the grocery product table
product_table.GroceryProductGuid.as_entity("product")
product_table.ProductGroup.as_entity("productgroup")

Now, if we list the tables as we did in the previous tutorial, we'll notice that entities have been assigned to each table.

In [5]:
display(catalog.list_tables())

id             name             type        status  \
0  68ef0d6c93cce39d676ca31a   GROCERYPRODUCT  dimension_table  PUBLIC_DRAFT   
1  68ef0d6b93cce39d676ca319     INVOICEITEMS       item_table  PUBLIC_DRAFT   
2  68ef0d6693cce39d676ca318   GROCERYINVOICE      event_table  PUBLIC_DRAFT   
3  68ef0d6293cce39d676ca317  GROCERYCUSTOMER        scd_table  PUBLIC_DRAFT   

                   entities                  created_at  
0   [product, productgroup]  2025-10-15T02:56:44.790000  
1  [item, invoice, product]  2025-10-15T02:56:43.248000  
2       [invoice, customer]  2025-10-15T02:56:39.032000  
3   [customer, frenchstate]  2025-10-15T02:56:34.333000

We can also list entities separately: 

In [6]:
display(catalog.list_entities())

id          name             serving_names  \
0  68ef0fd33b169e959799c247   frenchstate             [FRENCHSTATE]   
1  68ef0fd33b169e959799c246  productgroup            [PRODUCTGROUP]   
2  68ef0fd23b169e959799c245       product      [GROCERYPRODUCTGUID]   
3  68ef0fd23b169e959799c244          item  [GROCERYINVOICEITEMGUID]   
4  68ef0fd23b169e959799c243       invoice      [GROCERYINVOICEGUID]   
5  68ef0fd23b169e959799c242      customer     [GROCERYCUSTOMERGUID]   

                   created_at  
0  2025-10-15T03:06:59.366000  
1  2025-10-15T03:06:59.192000  
2  2025-10-15T03:06:59.006000  
3  2025-10-15T03:06:58.829000  
4  2025-10-15T03:06:58.647000  
5  2025-10-15T03:06:58.482000

And let's examine the relationships between entities, which FeatureByte has conveniently outlined for us:

In [7]:
display(catalog.list_relationships())

id relationship_type    entity related_entity  \
0  68ef0fd6bfd5aaec3c90f2e8      child_parent   product   productgroup   
1  68ef0fd5cf8a902261e4383e      child_parent      item        product   
2  68ef0fd56c7cac43b232de32      child_parent      item        invoice   
3  68ef0fd51b81baf0fe875d1e      child_parent   invoice       customer   
4  68ef0fd43474e35f2f07a843      child_parent  customer    frenchstate   

    relation_table relation_table_type  enabled                  created_at  \
0   GROCERYPRODUCT     dimension_table     True  2025-10-15T03:07:02.265000   
1     INVOICEITEMS          item_table     True  2025-10-15T03:07:01.815000   
2     INVOICEITEMS          item_table     True  2025-10-15T03:07:01.620000   
3   GROCERYINVOICE         event_table     True  2025-10-15T03:07:01.185000   
4  GROCERYCUSTOMER           scd_table     True  2025-10-15T03:07:00.809000   

  updated_at  
0       None  
1       None  
2       None  
3       None  
4       None

That's it for most important data modeling concepts in FeatureByte. 
In next tutorials we will look into concepts related to data cleaning and feature engineering. 

### For more details about concepts we discussed in this tutorial, feel free to explore:
- [More info on Entities](https://docs.featurebyte.com/latest/about/glossary/#entities-and-relationships)

#### SDK reference for
- [Entity](https://docs.featurebyte.com/latest/reference/core/entity/)
- [Catalog.create_entity()](https://docs.featurebyte.com/latest/reference/featurebyte.api.catalog.Catalog.create_entity/)
- [TableColumn.as_entity()](https://docs.featurebyte.com/latest/reference/featurebyte.api.base_table.TableColumn.as_entity/)